# L-PICOLA plotting

## Setup

In [32]:
import dataclasses
from pathlib import Path

import numpy as np
import pynbody as pb
from scipy import stats

import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots


pio.templates["latex"] = pio.templates["plotly_white"].update(
    layout=dict(
        colorway=px.colors.qualitative.D3,
        font=dict(
            family="CMU Serif",
            size=12
        )
    )
)

pio.templates.default = "latex"

## Config

In [33]:
SNAPSHOT_PATH = Path("../output/20251111_143301/output_z0p000")
PLOT_DIRECTORY = Path("./plots")

PLOT_POINTS = 100_000  # downsample for speed if needed

snapshot = pb.load(SNAPSHOT_PATH)

## Plotting

### 3D point cloud

In [84]:
snapshot.properties

{'omegaM0': 0.31,
 'omegaL0': 0.69,
 'boxsize': Unit("2.00e+02 Mpc a h**-1"),
 'a': 1.0,
 'h': 0.69,
 'time': Unit("9.55e-03 s Mpc a**1/2 km**-1 h**-1")}

In [ ]:
L = float(snapshot.properties.get('boxsize', 0.0))

# downsample (reuse existing variables if present)
pos = snapshot['pos'].view(np.ndarray)
idx = np.random.choice(pos.shape[0], size=PLOT_POINTS, replace=False)
pts_plot = pos[idx]

fig = go.Figure(data=[
    go.Scatter3d(
        x=pts_plot[:,0], y=pts_plot[:,1], z=pts_plot[:,2],
        mode='markers',
        marker=dict(size=1),
        name='Particles',
        opacity=0.2,
    )
])

# zoom out padding and camera
camera = dict(
    center=dict(x=0, y=0, z=-0.2)
)
fig.update_layout(
    title=f"Simulation results, z=0 (downsampled to {pts_plot.shape[0]} pts)",
    scene_aspectmode='data',
    margin=dict(l=0, r=0, b=0, t=40),
    scene=dict(
        xaxis_title='X [Mpc/h]',
        yaxis_title='Y [Mpc/h]',
        zaxis_title='Z [Mpc/h]',
        camera=camera,
    )
)
fig.show()
fig.write_image(PLOT_DIRECTORY / "snapshot_3d_scatter.pdf")

## Processing the snapshot

### Helpers

#### SnapshotData

In [35]:
@dataclasses.dataclass
class SnapshotData:
    X: np.ndarray
    Y: np.ndarray
    Z: np.ndarray
    mass: np.ndarray
    mins: np.ndarray
    maxs: np.ndarray
    _mean: np.float64 = None
    _mean_nz: np.float64 = None
    _median: np.float64 = None
    _median_nz: np.float64 = None
    _percentile_90: np.float64 = None
    _percentile_90_nz: np.float64 = None
    _std: np.float64 = None

    def duplicate(self):
        """Returns shallow copy of self."""
        return dataclasses.replace(self)
    
    @property
    def median(self):
        if self._median is None:
            self._median = np.median(self.mass)
        return self._median

    @property
    def mass_nz(self):
        return self.mass[self.mass > 0]

    @property
    def median_nz(self):
        if self._median_nz is None:
            self._median_nz = np.median(self.mass_nz) if self.mass_nz.size else np.float64(0.0)
        return self._median_nz

    @property
    def mean(self):
        if self._mean is None:
            self._mean = np.mean(self.mass)
        return self._mean
    
    @property
    def mean_nz(self):
        if self._mean_nz is None:
            self._mean_nz = np.mean(self.mass_nz) if self.mass_nz.size else np.float64(0.0)
        return self._mean_nz
    
    @property
    def percentile_90(self):
        if self._percentile_90 is None:
            self._percentile_90 = np.percentile(self.mass, 90)
        return self._percentile_90

    @property
    def percentile_90_nz(self):
        if self._percentile_90_nz is None:
            self._percentile_90_nz = np.percentile(self.mass_nz, 90) if self.mass_nz.size else np.float64(0.0)
        return self._percentile_90_nz

    @property
    def std(self):
        if self._std is None:
            self._std = np.std(self.mass, mean=self.mean)
        return self._std


In [36]:
def mass_grid_from_snapshot(snapshot: pb.snapshot.SimSnap, ngrid=64):
    """Computes a 3D mass density grid from the simulation `snapshot`."""
    pos = snapshot['pos']   # (N, 3)
    mass = snapshot['mass'] # (N,)

    mins = pos.min(axis=0)
    maxs = pos.max(axis=0)

    mass_grid, _ = np.histogramdd(
        pos,
        bins=ngrid,
        range=((mins[0], maxs[0]),
               (mins[1], maxs[1]),
               (mins[2], maxs[2])),
        weights=mass
    )

    ngrid = mass_grid.shape[0]
    mins = np.asarray(mins)
    maxs = np.asarray(maxs)

    # voxel size along each axis
    size = maxs - mins
    d = size / ngrid

    # coordinates of voxel centers in ORIGINAL units
    x_centers = mins[0] + (np.arange(ngrid) + 0.5) * d[0]
    y_centers = mins[1] + (np.arange(ngrid) + 0.5) * d[1]
    z_centers = mins[2] + (np.arange(ngrid) + 0.5) * d[2]

    # 3D mesh of centers
    X, Y, Z = np.meshgrid(x_centers, y_centers, z_centers, indexing='ij')

    values = mass_grid.astype(float)

    return SnapshotData(X=X, Y=Y, Z=Z, mass=values, mins=mins, maxs=maxs)

snapshot_data = mass_grid_from_snapshot(snapshot, ngrid=16)

#### Plot functions

In [37]:
def plot_meshgrid_isosurfaces(snapshot_data: SnapshotData, title="", n_isosurfaces=5, opacity=0.4):
    fig = go.Figure(
        data=go.Volume(
            x=snapshot_data.X.flatten(),
            y=snapshot_data.Y.flatten(),
            z=snapshot_data.Z.flatten(),
            value=snapshot_data.mass.flatten(),
            isomin=snapshot_data.mass.min(),
            isomax=snapshot_data.mass.max(),
            opacity=opacity,
            surface_count=n_isosurfaces,
            caps=dict(x_show=False, y_show=False, z_show=False),
            colorscale="Blues",
        )
    )

    fig.update_layout(scene_aspectmode="data", margin=dict(l=0, r=0, b=0, t=40), title=title)

    fig.show()


In [38]:
def get_histogram(data: np.ndarray, nbins=200, **kwargs):
    color = kwargs.pop("color", "cornflowerblue")

    counts, edges = np.histogram(data, bins=nbins)
    centers = 0.5 * (edges[:-1] + edges[1:])
    widths  = edges[1:] - edges[:-1]
    return go.Bar(x=centers, y=counts, width=widths, marker=dict(color=color), **kwargs)


def plot_histogram(data: np.ndarray, title="", log_x=False, log_y=False, nbins=200, layout_kwargs={}, traces_kwargs={}):
    fig = go.Figure(get_histogram(data, nbins=nbins, **traces_kwargs))
    fig.update_layout(
        bargap=0,
        template=dict(data=dict(bar=[dict(marker=dict(line=dict(width=0)))])),
        title=title,
        xaxis=dict(type="log" if log_x else "linear"),
        yaxis=dict(type="log" if log_y else "linear"),
        **layout_kwargs,
    )
    return fig


### Original mesh

In [39]:
plot_meshgrid_isosurfaces(snapshot_data, title="Mass density isosurfaces at z=0")

In [40]:
plot_histogram(title="Mass histogram", data=snapshot_data.mass.flatten())

### Log10 mesh

In [41]:
snapshot_data_log = snapshot_data.duplicate()
snapshot_data_log.mass = np.log10(snapshot_data_log.mass + 1e-30)

plot_meshgrid_isosurfaces(snapshot_data_log, title="Log10 Mass density isosurfaces at z=0")

In [42]:
plot_histogram(title="Log10 Mass histogram", data=snapshot_data_log.mass.flatten())

### $(1 - e^{-data})$-normalized

#### mean

In [43]:
snapshot_data_e_normalized_mean = snapshot_data.duplicate()
snapshot_data_e_normalized_mean.mass = 1 - np.exp(-snapshot_data_e_normalized_mean.mass / snapshot_data_e_normalized_mean.mass.mean())

plot_meshgrid_isosurfaces(snapshot_data_e_normalized_mean, title="Exp-normalized Mass / mean density isosurfaces at z=0")

In [44]:
plot_histogram(title="Exp-normalized Mass / mean histogram", data=snapshot_data_e_normalized_mean.mass.flatten())

#### median

In [45]:
snapshot_data_e_normalized_median = snapshot_data.duplicate()
snapshot_data_e_normalized_median.mass = 1 - np.exp(-snapshot_data_e_normalized_median.mass / snapshot_data_e_normalized_median.median)

plot_meshgrid_isosurfaces(snapshot_data_e_normalized_median, title="Exp-normalized Mass / median density isosurfaces at z=0")

In [46]:
plot_histogram(title="Exp-normalized Mass / median histogram", data=snapshot_data_e_normalized_median.mass.flatten())

### $(1 - 10^{-data})$-normalized

#### mean

In [47]:
snapshot_data_10_normalized_mean = snapshot_data.duplicate()
snapshot_data_10_normalized_mean.mass = 1 - 10 ** (-snapshot_data_10_normalized_mean.mass / snapshot_data_10_normalized_mean.mass.mean())

plot_meshgrid_isosurfaces(snapshot_data_10_normalized_mean, title="10-normalized Mass density / mean isosurfaces at z=0")

In [48]:
plot_histogram(title="10-normalized Mass / mean histogram", data=snapshot_data_10_normalized_mean.mass.flatten())

#### median

In [49]:
snapshot_data_10_normalized_median = snapshot_data.duplicate()
snapshot_data_10_normalized_median.mass = 1 - 10 ** (-snapshot_data_10_normalized_median.mass / snapshot_data_10_normalized_median.median)

plot_meshgrid_isosurfaces(snapshot_data_10_normalized_median, title="10-normalized Mass density / median isosurfaces at z=0")

In [50]:
plot_histogram(title="10-normalized Mass / median histogram", data=snapshot_data_10_normalized_median.mass.flatten())

### Summary

In [ ]:
cube_data = [
    (snapshot_data, "Original Mass Density"),
    (snapshot_data_log, "Log10 Mass Density"),
    (snapshot_data_e_normalized_mean, "Exp-Normalized / Mean"),
    (snapshot_data_e_normalized_median, "Exp-Normalized / Median"),
    (snapshot_data_10_normalized_mean, "10-Normalized / Mean"),
    (snapshot_data_10_normalized_median, "10-Normalized / Median"),
]
n_cubes = len(cube_data)

# Create subplot grid: 2 rows (top: cubes, bottom: histograms)
fig = make_subplots(
    rows=2, cols=n_cubes,
    subplot_titles=[title for _, title in cube_data] + [f"{title} Histogram<br>(std: {data.std:.3f})" for data, title in cube_data],
    specs=[[{'type': 'scene'}]*n_cubes, [{'type': 'xy'}]*n_cubes],
    vertical_spacing=0.1,
)

# Add cubes (isosurfaces) to top row
for i, (data, title) in enumerate(cube_data):
    fig.add_trace(
        go.Volume(
            x=data.X.flatten(),
            y=data.Y.flatten(),
            z=data.Z.flatten(),
            value=data.mass.flatten(),
            isomin=data.mass.min(),
            isomax=data.mass.max(),
            opacity=0.3,
            surface_count=5,
            caps=dict(x_show=False, y_show=False, z_show=False),
            colorscale="Blues",
            showscale=False,
        ),
        row=1, col=i+1
    ),
    

# Add histograms to bottom row
for i, (data, title) in enumerate(cube_data):
    fig.add_trace(
        get_histogram(data.mass.flatten(), nbins=20),
        row=2, col=i+1
    )

fig.update_layout(
    height=600,
    width=300*n_cubes,
    title_text="Comparison of Mass Density Cubes and Histograms",
    showlegend=False,
    margin=dict(l=0, r=0, t=60, b=40),
)
for i in range(n_cubes):
    fig.update_scenes(
        row=1,
        col=i+1,
        camera=dict(
            eye=dict(x=2, y=2, z=2),
            center=dict(x=0, y=0, z=-0.2)
        ),
        xaxis=dict(title=dict(text="X [Mpc/h]", font=dict(size=10)), tickfont=dict(size=8)),
        yaxis=dict(title=dict(text="Y [Mpc/h]", font=dict(size=10)), tickfont=dict(size=8)),
        zaxis=dict(title=dict(text="Z [Mpc/h]", font=dict(size=10)), tickfont=dict(size=8)),
    )

fig.show()
fig.write_image(PLOT_DIRECTORY / "summary_low_resolution.pdf")

## Dealing with data in high resolution

### Original data

In [52]:
hd_snapshot_data = mass_grid_from_snapshot(snapshot, ngrid=256)
np.save("data/hd_snapshot_data_mass.npy", hd_snapshot_data.mass)

plot_histogram(title="Mass histogram without normalization", data=hd_snapshot_data.mass.flatten(), log_y=True)

In [53]:
plot_histogram(title="Mass histogram without normalization", data=hd_snapshot_data.mass.flatten(), nbins=5000, log_y=True)

### $(1 - e^{-data})$-normalized

#### mean

In [54]:
hd_snapshot_data_e_normalized_mean = hd_snapshot_data.duplicate()
hd_snapshot_data_e_normalized_mean.mass = 1 - np.exp(-hd_snapshot_data_e_normalized_mean.mass / (hd_snapshot_data_e_normalized_mean.mean_nz))
np.save("data/hd_snapshot_data_e_normalized_mean_mass.npy", hd_snapshot_data_e_normalized_mean.mass)

plot_histogram(title="Exp-normalized Mass / mean histogram", data=hd_snapshot_data_e_normalized_mean.mass.flatten(), log_y=True)

#### mean^2

In [55]:
hd_snapshot_data_e_normalized_mean_square = hd_snapshot_data.duplicate()
hd_snapshot_data_e_normalized_mean_square.mass = 1 - np.exp(-hd_snapshot_data_e_normalized_mean_square.mass / (hd_snapshot_data_e_normalized_mean_square.mean_nz**2))
np.save("data/hd_snapshot_data_e_normalized_mean_square_mass.npy", hd_snapshot_data_e_normalized_mean_square.mass)

plot_histogram(title="Exp-normalized Mass / mean^2 histogram", data=hd_snapshot_data_e_normalized_mean_square.mass.flatten(), log_y=True)

#### median

In [56]:
hd_snapshot_data_e_normalized_median = hd_snapshot_data.duplicate()
hd_snapshot_data_e_normalized_median.mass = 1 - np.exp(-hd_snapshot_data_e_normalized_median.mass / hd_snapshot_data_e_normalized_median.median_nz)
np.save("data/hd_snapshot_data_e_normalized_median_mass.npy", hd_snapshot_data_e_normalized_median.mass)

plot_histogram(title="Exp-normalized Mass / median histogram", data=hd_snapshot_data_e_normalized_median.mass.flatten(), log_y=True)

#### medain^2

In [57]:
hd_snapshot_data_e_normalized_median_square = hd_snapshot_data.duplicate()
hd_snapshot_data_e_normalized_median_square.mass = 1 - np.exp(-hd_snapshot_data_e_normalized_median_square.mass / hd_snapshot_data_e_normalized_median_square.median_nz**2)
np.save("data/hd_snapshot_data_e_normalized_median_square_mass.npy", hd_snapshot_data_e_normalized_median_square.mass)

plot_histogram(title="Exp-normalized Mass / median^2 histogram", data=hd_snapshot_data_e_normalized_median_square.mass.flatten(), log_y=True)

In [58]:
hd_snapshot_data_e_normalized_median_cubed = hd_snapshot_data.duplicate()
hd_snapshot_data_e_normalized_median_cubed.mass = 1 - np.exp(-hd_snapshot_data_e_normalized_median_cubed.mass / hd_snapshot_data_e_normalized_median_cubed.median_nz**3)
np.save("data/hd_snapshot_data_e_normalized_median_cubed_mass.npy", hd_snapshot_data_e_normalized_median_cubed.mass)

plot_histogram(title="Exp-normalized Mass / median^3 histogram", data=hd_snapshot_data_e_normalized_median_cubed.mass.flatten(), log_y=True)

### Summary

In [94]:
datasets = [
    (hd_snapshot_data, "Original"),
    (hd_snapshot_data_e_normalized_mean, "Exp-normalized / mean"),
    (hd_snapshot_data_e_normalized_mean_square, "Exp-normalized / mean^2"),
    (hd_snapshot_data_e_normalized_median, "Exp-normalized / median"),
    (hd_snapshot_data_e_normalized_median_square, "Exp-normalized / median^2"),
]

n = len(datasets)
fig = make_subplots(rows=1, cols=n, subplot_titles=[f"{title}<br>(std: {data.std:.3f})" for data, title in datasets])

for i, (data, title) in enumerate(datasets, start=1):
    fig.add_trace(
        get_histogram(data.mass.flatten(), nbins=20),
        row=1, col=i
    )
    fig.update_yaxes(type="log", row=1, col=i)

fig.update_layout(
    title_text="High Resolution Data Normalization Histograms",
    showlegend=False,
    width=300*n,
    height=400,
    margin=dict(l=0, r=0, t=100, b=40),
)
fig.show()
fig.write_image(PLOT_DIRECTORY / "summary_high_resolution.pdf")